In [7]:
!pip install langchain langchain_core langgraph langchain_groq langgraph pydantic -U faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.2/67.2 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 438.4/438.4 kB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 444.2/444.2 kB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.3/31.3 MB 25.0 MB/s eta 0:00:00
  Attempting uninstall: pydantic
    Found existing installation: pydantic 2.11.4
    Uninstalling pydantic-2.11.4:
      Successfully uninstalled pydantic-2.11.4
  Attempting uninstall: langchain_core
    Found existing installation: langchain-core 0.3.60
    Uninstalling langchain-core-0.3.60:
      Successfully uninstalled langchain-core-0.3.60


In [1]:
import os
import ast
from pydantic import BaseModel, Field
from typing import Optional
import pandas as pd
from langchain_core.messages import SystemMessage, HumanMessage
from langgraph.graph import StateGraph, START, END
from langchain_core.tools import tool
from sentence_transformers import SentenceTransformer
import numpy as np
import faiss


from google.colab import userdata
os.environ['GROQ_API_KEY']=userdata.get('groq_api_subash')

class State(BaseModel):
  topic: str
  business_details: Optional[dict]
  ideator_response: Optional[str] = None
  critic_response: Optional[str]=None
  improver_response: Optional[str]=None
  validator_response: Optional[str]=None
  validator_defense1: Optional[str]=None
  validator_defense2: Optional[str]=None
  validator_defense3: Optional[str]=None


In [2]:
from langchain_groq import ChatGroq
from langgraph.prebuilt import create_react_agent

llm = ChatGroq(
    model="llama3-8b-8192",
    temperature=0.3,
    max_tokens=500,

)

ideator_llm = llm
critic_llm = llm
improver_llm = llm
validator_llm = llm


In [3]:

ST = SentenceTransformer('mixedbread-ai/mxbai-embed-large-v1')
class QueryFormatter(BaseModel):
    video_topic: str = Field(description="The video topic that user passes to the agent")

@tool("influencer's data-retrieval-tool", args_schema=QueryFormatter, return_direct=False,description="Retrieve influencer-related data for a given query.")
def retrieve_tool(video_topic):
    '''
    Always invoke this tool.
    Retrieve influencer's data by semantic search of **video topic**.
    '''
    # === Load CSV ===
    csv_path = 'extracted_data.csv'
    df = pd.read_csv(csv_path)

    # === Parse stored embeddings ===
    df['embeddings'] = df['embeddings'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)
    embeddings = np.vstack(df['embeddings'].values).astype('float32')

    # === Build FAISS index ===
    dimension = embeddings.shape[1]
    index = faiss.IndexFlatL2(dimension)
    index.add(embeddings)

    # === Load SentenceTransformer model ===

    # === Encode the query and search ===
    query_embedding = ST.encode(str(video_topic)).reshape(1, -1).astype('float32')
    top_k=7
    distances, indices = index.search(query_embedding, top_k)



    # === Format results ===
    outer_list = []
    for i, idx in enumerate(indices[0]):
        res = {
            'rank': i + 1,
            'username': df.iloc[idx]['username'],
            'story': df.iloc[idx]['story'],
            'visible_text_or_brandings': df.iloc[idx]['story'],
            'likesCount': df.iloc[idx]['likesCount'],
            'commentCount': df.iloc[idx]['commentCount'],
        }

        inner_list = []
        inner_list.append(f"[{res['rank']}]. The influencer name is: **{res['username']}** — Likes: **{res['likesCount']}**, Comments: **{res['commentCount']}**")
        inner_list.append(f"The story of that particular video is:\n{res['story']}")
        inner_list.append(f"The branding or promotion done is:\n{res['visible_text_or_brandings']}")

        outer_list.append(inner_list)

    return str(outer_list)

# retrieve_tool('I want to promote my restaurant')

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [4]:

def ideator(state:State):
  tools=[retrieve_tool]
  react_agent=create_react_agent(
    model=llm,
    tools=tools
  )
  template = f'''
  You are an expert video content strategist who generates the storyline of a video in exactly 300 words..

Your task is to generate a **detailed and creative storyline** for a promotional video on the **given topic**. The storyline should be structured, engaging, and highly relevant to the following **business details**.
Another important thing is that you have to give the response  focusing on the response of the tool provided to you. The tool contains the video stories and contents created by the influencers.
Use that responses of tool for your reference. You can use your creativity but inside the boundary of tool's response.

---

 **Video Topic**:
{state.topic}

**Business Details**:
{state.business_details}



---

**Important Instructions**:
- Creatively connect the image cues to make the storyline compelling. (If provided).
- Structure the storyline logically (e.g., beginning, middle, end), showing what scenes or visuals to include.
- Match the tone and depth to the business type (e.g., fun, luxurious, emotional, professional).

Now, generate the final storyline for the video topic..
  '''
  messages = [SystemMessage(content=template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n''')]

  response = react_agent.invoke({'messages':messages})
  response = response['messages'][-1].content
  state.ideator_response = response
  print('Ideator Generated the story')
  return state





In [5]:
def critic(state:State):
  tools=[retrieve_tool]
  react_agent=create_react_agent(
    model=llm,
    tools=tools
  )
  critic_template = f'''
  You are an expert evaluator and suggestion recommender. Your role is to carefully read the story generated by the Ideator and assess it based on the given video topic, business details, and the tool's response.

  Your task is to **critically evaluate** the storyline of a promotional video provided below from ideator. The storyline was generated based on a given video topic and business details. Additionally, the tool's response contains existing influencer-style stories or content for reference, which you must **closely consider** to guide your evaluation.

  ---

   **Video Topic**:
  {state.topic}

   **Business Details**:
  {state.business_details}

   **Generated Storyline from ideator**:
  {state.ideator_response}


  ---

   **Your Task as the Critic**:

  1. **Evaluate the Storyline**: Analyze the structure, creativity, tone, and alignment with the business type and audience.
  2. **Compare with Tool's Response**: Ensure the storyline stays within the creative boundaries and tone of the influencer-style content in the tool response.
  3. **Identify Weaknesses**: Point out inconsistencies, missing elements, weak hooks, structural flaws, or areas lacking emotional or persuasive power.
  4. **Suggest Improvements**: Provide clear, actionable suggestions to improve the storyline.

  **Output**:
  You have to just suggest the improvements in your output in around 100 words only.
  '''

  messages = [SystemMessage(content=critic_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n. The business_details is\n{state.business_details}\n''')]

  response = react_agent.invoke({'messages':messages})
  response = response['messages'][-1].content
  state.critic_response = response
  print('Critic Evaluated the story')

  return state


In [6]:
def improver(state:State):
  react_agent=create_react_agent(
    model=llm,
    tools=[]
  )
  improver_template = f'''
  You are a professional video content editor and creative storyteller. Your job is to improve the storyline originally generated by the Ideator using the detailed feedback provided by the Critic.

  The story was written for a promotional video based on a specific topic and business context. You must revise it while staying aligned with the given business needs and creative direction. The improvement suggestions come from a Critic who has evaluated the structure, tone, creativity, and alignment of the original story.

  ---

  **Video Topic**:
  {state.topic}

  **Business Details**:
  {state.business_details}

  **Original Storyline from Ideator**:
  {state.ideator_response}

  **Critic's Suggestions for Improvement**:
  {state.critic_response}

  ---

  **Your Task**:

  - Carefully read the original story and the critic’s suggestions.
  - Revise and enhance the storyline, correcting flaws and adding the suggested improvements.
  - Keep the tone, structure, and message appropriate to the business type and the influencer-style content.
  - Make sure the final story is structured, compelling, and exactly **300 words** in length.

  Now, generate the **final improved storyline** for the video.
  '''


  messages = [SystemMessage(content=improver_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n The business_details is:\n{state.business_details}''')]

  response = react_agent.invoke({'messages':messages})
  response = response['messages'][-1].content
  state.improver_response = response
  print('Improver Improvred the story')

  return state


In [7]:
class ValidationFormatter(BaseModel):
  result: str = Field(description="Returns **validated** if the story is validated. Returns **not validated** if story is not validated.")

def validator(state:State):
  tools=[retrieve_tool]

  react_agent=create_react_agent(
    model=llm,
    tools=tools,
    # response_format=ValidationFormatter
  )
  validator_template = f'''
  You are a strict and unbiased judge responsible for evaluating whether a promotional video storyline is ready for publishing.

  You will be given the video topic, business details, and the final version of the storyline (after improvement). Your task is to assess if this storyline meets all necessary standards in terms of:

  - Relevance to the video topic
  - Alignment with the business context
  - Logical structure (beginning, middle, end)
  - Tone matching the business type
  - Creativity and clarity

  You can also use the tool's response as your reference to make the validation. The tool's response includes existing influencer-style stories or content for reference.

  ---


  **Video Topic**:
  {state.topic}

  **Business Details**:
  {state.business_details}

  **Final Storyline from Improver**:
  {state.improver_response}

  ---

  **Validation Criteria**:

  - Is the story **fully aligned** with the topic, business details and the tool's response?
  - Does the structure flow logically and effectively?
  - Does it feel complete and professional to use this story to create a video?

  ---

  **Output Instruction**:
  Respond strictly just with one of the following values:

  - `validated` – if the story meets all the criteria and is validated.
  - `not validated` – if it fails to meet any key criteria and needs further improvement.
  '''



  messages = [SystemMessage(content=validator_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n The business_details is:\n{state.business_details}''')]

  response = llm.with_structured_output(ValidationFormatter).invoke(messages)
  print('Validator response:',response)
  state.validator_response = response.result
  return state

In [8]:
def validator_defense1(state:State):
  tools=[retrieve_tool]

  react_agent=create_react_agent(
    model=llm,
    tools=tools,
    # response_format=ValidationFormatter
  )
  validator_template = f'''
  You are a strict and unbiased judge responsible for evaluating whether a promotional video storyline is ready for publishing.

  You will be given the video topic, business details, and the final version of the storyline (after improvement). Your task is to assess if this storyline meets all necessary standards in terms of:

  - Relevance to the video topic
  - Alignment with the business context
  - Logical structure (beginning, middle, end)
  - Tone matching the business type
  - Creativity and clarity

  You can also use the tool's response as your reference to make the validation. The tool's response includes existing influencer-style stories or content for reference.

  ---


  **Video Topic**:
  {state.topic}

  **Business Details**:
  {state.business_details}

  **Final Storyline from Improver**:
  {state.improver_response}

  ---

  **Validation Criteria**:

  - Is the story **fully aligned** with the topic, business details and the tool's response?
  - Does the structure flow logically and effectively?
  - Does it feel complete and professional to use this story to create a video?

  ---

  **Output Instruction**:
  Respond strictly just with one of the following values:

  - `validated` – if the story meets all the criteria and is validated.
  - `not validated` – if it fails to meet any key criteria and needs further improvement.
  '''



  messages = [SystemMessage(content=validator_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n The business_details is:\n{state.business_details}''')]

  response = llm.with_structured_output(ValidationFormatter).invoke(messages)
  print('Validator defense 1 response:',response)
  state.validator_defense1 = response.result
  return state


def validator_defense2(state:State):
  tools=[retrieve_tool]

  react_agent=create_react_agent(
    model=llm,
    tools=tools,
    # response_format=ValidationFormatter
  )
  validator_template = f'''
  You are a strict and unbiased judge responsible for evaluating whether a promotional video storyline is ready for publishing.

  You will be given the video topic, business details, and the final version of the storyline (after improvement). Your task is to assess if this storyline meets all necessary standards in terms of:

  - Relevance to the video topic
  - Alignment with the business context
  - Logical structure (beginning, middle, end)
  - Tone matching the business type
  - Creativity and clarity

  You can also use the tool's response as your reference to make the validation. The tool's response includes existing influencer-style stories or content for reference.

  ---


  **Video Topic**:
  {state.topic}

  **Business Details**:
  {state.business_details}

  **Final Storyline from Improver**:
  {state.improver_response}

  ---

  **Validation Criteria**:

  - Is the story **fully aligned** with the topic, business details and the tool's response?
  - Does the structure flow logically and effectively?
  - Does it feel complete and professional to use this story to create a video?

  ---

  **Output Instruction**:
  Respond strictly just with one of the following values:

  - `validated` – if the story meets all the criteria and is validated.
  - `not validated` – if it fails to meet any key criteria and needs further improvement.
  '''



  messages = [SystemMessage(content=validator_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n The business_details is:\n{state.business_details}''')]

  response = llm.with_structured_output(ValidationFormatter).invoke(messages)
  print('Validator defense 2 response:',response)
  state.validator_defense2 = response.result
  return state


def validator_defense3(state:State):
  tools=[retrieve_tool]

  react_agent=create_react_agent(
    model=llm,
    tools=tools,
    # response_format=ValidationFormatter
  )
  validator_template = f'''
  You are a strict and unbiased judge responsible for evaluating whether a promotional video storyline is ready for publishing.

  You will be given the video topic, business details, and the final version of the storyline (after improvement). Your task is to assess if this storyline meets all necessary standards in terms of:

  - Relevance to the video topic
  - Alignment with the business context
  - Logical structure (beginning, middle, end)
  - Tone matching the business type
  - Creativity and clarity

  You can also use the tool's response as your reference to make the validation. The tool's response includes existing influencer-style stories or content for reference.

  ---


  **Video Topic**:
  {state.topic}

  **Business Details**:
  {state.business_details}

  **Final Storyline from Improver**:
  {state.improver_response}

  ---

  **Validation Criteria**:

  - Is the story **fully aligned** with the topic, business details and the tool's response?
  - Does the structure flow logically and effectively?
  - Does it feel complete and professional to use this story to create a video?

  ---

  **Output Instruction**:
  Respond strictly just with one of the following values:

  - `validated` – if the story meets all the criteria and is validated.
  - `not validated` – if it fails to meet any key criteria and needs further improvement.
  '''



  messages = [SystemMessage(content=validator_template),
                HumanMessage(content=f'''The topic of the video is:\n{state.topic}\n The business_details is:\n{state.business_details}''')]

  response = llm.with_structured_output(ValidationFormatter).invoke(messages)
  print('Validator defense 3 response:',response)
  state.validator_defense3 = response.result
  return state

In [9]:
def route1_after_validation(state:State):
  if 'not validated' in state.validator_response:
    return False
  else:
    return True

def route2_after_validation(state:State):
  if 'not validated' in state.validator_defense1:
    return False
  else:
    return True
def route3_after_validation(state:State):
  if 'not validated' in state.validator_defense2:
    return False
  else:
    return True
def route4_after_validation(state:State):
  if 'not validated' in state.validator_defense3:
    return False
  else:
    return True

In [10]:
graph_builder= StateGraph(State)
graph_builder.add_node(ideator)
graph_builder.add_node(critic)
graph_builder.add_node(improver)
graph_builder.add_node(validator)
graph_builder.add_node(validator_defense1)
graph_builder.add_node(validator_defense2)
graph_builder.add_node(validator_defense3)


graph_builder.add_edge(START, "ideator")  # Start the graph with node_1
graph_builder.add_edge("ideator", "critic")
graph_builder.add_edge("critic", "improver")
graph_builder.add_edge("improver", "validator")
graph_builder.add_edge("validator", "validator_defense1")
graph_builder.add_edge("validator_defense1", "validator_defense2")
graph_builder.add_edge("validator_defense2", "validator_defense3")
graph_builder.add_edge("validator_defense3", END)

# Use conditional routing from validator
graph_builder.add_conditional_edges("validator", route1_after_validation,{False:'ideator',True:validator_defense1})
graph_builder.add_conditional_edges("validator_defense1", route2_after_validation,{False:'ideator',True:validator_defense2})
graph_builder.add_conditional_edges("validator_defense2", route3_after_validation,{False:'ideator',True:validator_defense3})
graph_builder.add_conditional_edges("validator_defense3", route4_after_validation,{False:'ideator',True:END})

graph = graph_builder.compile()


ValueError: 'validator_defense1' is already being used as a state key

In [ ]:
from IPython.display import Image, display

try:
    display(Image(graph.get_graph().draw_mermaid_png()))
except Exception:
    # This requires some extra dependencies and is optional
    pass

In [18]:
state = graph.invoke({"topic": "I want to promote my restaurant in lakeside",
                      "business_details": {"business_type": "restaurant", "platform": "instagram", "target_audience": "youths", "business_goals": "to go global", "offerings": "nepali foods", "Challenges_faced": "finding new customers, attracting large customers"}
                      })

Ideator Generated the story
Critic Evaluated the story
Improver Improvred the story
Validator response: result='validated'


In [22]:
state['validator_response']

'validated'

In [19]:
state['improver_response']

'Here is the revised storyline for the promotional video:\n\n**Title:** "Experience the Flavors of Nepal at [Your Restaurant Name] in Lakeside"\n\n**Scene 1:** (0:00 - 0:30)\n\n* Opening shot of a stunning visual of the restaurant\'s exterior, with a warm and inviting glow emanating from the windows.\n* Voiceover: "Imagine a place where the beauty of Lakeside meets the flavors of Nepal. Welcome to [Your Restaurant Name], where every bite is a journey to the Himalayas."\n\n**Scene 2:** (0:30 - 1:00)\n\n* Cut to a shot of a group of friends laughing and chatting while enjoying their meals at the restaurant.\n* Voiceover: "Our restaurant is more than just a place to eat - it\'s a gathering spot for friends and family to share in the joy of good food and good company."\n\n**Scene 3:** (1:00 - 1:30)\n\n* Cut to a shot of the restaurant\'s chefs preparing traditional Nepali dishes, with close-ups of the sizzling pans and aromatic spices.\n* Voiceover: "Our chefs use only the freshest ingredi

In [13]:
state['critic_response']


"Based on the generated storyline, I would suggest the following improvements:\n\n* The storyline is quite generic and doesn't specifically highlight the unique aspects of the restaurant or its offerings. Consider incorporating more specific details about the restaurant's menu, ambiance, or staff to make it more engaging.\n* The storyline focuses more on the influencer's experience rather than the restaurant itself. Consider shifting the focus to the restaurant and its offerings to make it more relevant to the target audience.\n* The storyline could benefit from a clearer call-to-action (CTA) to encourage viewers to take action, such as visiting the restaurant or trying out a specific dish.\n\nOverall, the storyline has potential but could be improved by incorporating more specific details about the restaurant and its offerings, and by shifting the focus to the restaurant itself rather than the influencer's experience."

In [14]:
state['ideator_response']


'Here is a detailed and creative storyline for a promotional video on your restaurant:\n\n**Title:** "A Taste of Nepal: Discover the Flavors of Home"\n\n**Scene 1:** (0:00 - 0:30)\n\n* Opening shot of a bustling street in Kathmandu, Nepal, with the sound of traditional Nepali music playing in the background.\n* Cut to a shot of your restaurant\'s exterior, with a sign that reads "Nepali Food" in bold letters.\n* The camera pans inside the restaurant, showing the cozy and inviting atmosphere.\n\n**Scene 2:** (0:30 - 1:00)\n\n* Cut to a shot of a group of friends gathered around a table, enjoying a meal together.\n* The camera zooms in on the dishes they\'re eating, showcasing the variety of Nepali cuisine your restaurant offers.\n* The friends are laughing and chatting, enjoying each other\'s company.\n\n**Scene 3:** (1:00 - 1:30)\n\n* Cut to a shot of the chef, expertly preparing a traditional Nepali dish in the kitchen.\n* The camera shows the sizzling sounds and aromas of the cooking